This notebook plots the band alignment of materials using the data from Materials Project.

In [2]:
import math
import numpy as np
import matplotlib.pyplot as plt
import bisect
import itertools
import copy
import operator
from matplotlib.ticker import AutoMinorLocator
import matplotlib as mpl
mpl.rcParams['axes.linewidth'] = 2.0
csfont = {'fontname':'Times New Roman'}

In the next cell, specify the MPIDs for he desired materials.  Order is not important, they will be sorted automatically.

In [3]:
IDsToPlot=[886,554278,352,10390,19342,5238,4840,3839,19833,22386,22736,22811,546794,19921,856,570136,22883,1143,2920,
           661,672,804,22205,7631,2133,2172,1550,2624,2691,406,2534,2490,1156,20305,20012,10695,1190,2176,361,1132,
           23251,1265,715434,32,149]

The next slide is the main section.

In [6]:
ExpDat=np.genfromtxt('UserCNLData_Exp.txt')
ExpCNL=[]
MPData=np.genfromtxt('CNData_DensityEHullNAt_CompENeg_GapCorrCNL0.txt',dtype=None) #MP data with gap correction, CNL at 0
AllIDs=[]
AllCNLs=[]
AllGaps=[]
AllVBMs=[]
for i in range(0,len(MPData)):
    AllIDs.append(MPData[i][0])
    AllCNLs.append(MPData[i][1])
    AllGaps.append(MPData[i][2])
    AllVBMs.append(MPData[i][4])
FilteredIDs=np.array([i[0] for i in MPData])
FilteredDataIndices=[np.where(FilteredIDs==a)[0] for a in IDsToPlot]
FilteredDataIndices=[item for sublist in FilteredDataIndices for item in sublist]

#Import list of descriptors for sym group and list of chemical formulas
#both these files have the same indexing
DescriptorsData=np.genfromtxt('Descriptors.txt',dtype=None)
Formulas=np.genfromtxt('ChemComps.txt',dtype=None) #Only need chemical formulas, not separated names
allIDs=np.array([i[0] for i in DescriptorsData])
FullDataIndices=[np.where(allIDs==a)[0] for a in IDsToPlot]
FullDataIndices=[x for sublist in FullDataIndices for x in sublist]

#Collect MPID,VBM,CBM,Formula,SymGroup#
AllData=[[i,MPData[b][4],MPData[b][5],MPData[b][7],DescriptorsData[c][4]] for (i,b,c) in zip(IDsToPlot,FilteredDataIndices,FullDataIndices)]
for item in AllData:
    print(item)
AllData.sort(key = operator.itemgetter(4, 3)) #Sort by sym group number then by name
#for i in range(0,len(AllData)):
#    print AllData[i]
MPVBM=[AllData[a][1] for a in range(0,len(AllData))]
MPCBM=[AllData[a][2] for a in range(0,len(AllData))]

#Put user data into arrays and shifts CNL for comparison with MP
for i in range(0,len(AllData)):   
    if AllData[i][0] in ExpDat:
        ind1=np.where(ExpDat==AllData[i][0])[0][0]
        ExpCNL.append(ExpDat[ind1][1]+AllData[i][1])
        #print(AllData[i][0],AllData[i][3])
    else:
        ExpCNL.append(1000.0)

    
#print CitrineErr      
lowerVBM=[-1000]*len(AllData) #For bar plotting purposes
upperCBM=[1000]*len(AllData)

#hfont = {'fontname':'Times New Roman'}
x=np.arange(len(AllData))
xticks=[]
y=np.arange(-10,10,1)
yticks=np.arange(-10,10,1)
for i in np.arange(0,len(AllData)):
    xticks.append(AllData[i][3])
#print(xticks)
plt.xticks(rotation=90)
plt.bar(x,lowerVBM,1.0,bottom=MPVBM,color='b',alpha=0.8,align='center',edgecolor='b',label='Materials Project Bands')
plt.bar(x,upperCBM,1.0,bottom=MPCBM,color='r',alpha=0.8,edgecolor='r',align='center')
plt.plot(x,ExpCNL,linestyle='None',marker='h',color='m',markersize=12,label=r'E$_{CN,Exp}$')

ml = AutoMinorLocator(4)
plt.tick_params(which='both', width=2)
plt.tick_params(which='major', length=6)
plt.tick_params(which='minor', length=4)
plt.plot([-10,max(x)+10],[0,0],'--k',linewidth=2.0)
plt.xticks(x, xticks, fontsize=20,**csfont)
plt.yticks(y,yticks,fontsize=28,**csfont)
plt.gca().xaxis.grid(True,linestyle='--',linewidth=2.0)
plt.axis([-.5, len(AllData)-.5, -6,4])
plt.ylabel(r"$\rm{E-E_\mathrm{BP} (eV)}$",fontsize=40,**csfont)
plt.tick_params(axis='both', which='major', labelsize=20)
plt.axes().yaxis.set_minor_locator(ml)
plt.show() 


/usr/lib/pymodules/python2.7/matplotlib/font_manager.py:1236: UserWarning: findfont: Font family ['Times New Roman'] not found. Falling back to Bitstream Vera Sans
  (prop.get_family(), self.defaultFamily[fontext]))
/usr/lib/pymodules/python2.7/matplotlib/font_manager.py:1246: UserWarning: findfont: Could not match :family=Bitstream Vera Sans:style=normal:variant=normal:weight=normal:stretch=normal:size=20.0. Returning /usr/share/matplotlib/mpl-data/fonts/ttf/cmb10.ttf
  UserWarning)
/usr/lib/pymodules/python2.7/matplotlib/font_manager.py:1246: UserWarning: findfont: Could not match :family=Bitstream Vera Sans:style=normal:variant=normal:weight=normal:stretch=normal:size=40.0. Returning /usr/share/matplotlib/mpl-data/fonts/ttf/cmb10.ttf
  UserWarning)


[886, -3.2988919999999999, 0.32089200000000001, 'Ga2O3', 12]
[554278, -1.3952142857000001, 1.7762142857000001, 'TiO2', 12]
[352, -2.8799999999999999, 3.02, 'HfO2', 14]
[10390, -1.224998, 1.3409979999999999, 'Ta2O5', 15]
[19342, -1.734442, 0.97544200000000003, 'WO3', 60]
[5238, -1.374344, 0.490344, 'GaCuS2', 122]
[4840, -1.015808, -0.046191999999999997, 'GaCuSe2', 122]
[3839, -0.70382199999999995, 0.48382199999999997, 'GaCuTe2', 122]
[19833, -1.362924, 0.056924000000000002, 'InAgS2', 122]
[22386, -0.78681000000000001, 0.21381, 'InAgTe2', 122]
[22736, -1.132892, -0.20910799999999999, 'InCuS2', 122]
[22811, -0.95837000000000006, -0.038629999999999998, 'InCuSe2', 122]
[546794, -5.8125, 3.9885000000000002, 'SiO2', 122]
[19921, -1.1092777778, 1.4502777778, 'PbO', 129]
[856, -3.5342500000000001, -0.14174999999999999, 'SnO2', 136]
[570136, -1.9432940000000001, 1.1682939999999999, 'CuI', 156]
[22883, -1.4804999999999999, 1.1845000000000001, 'PbI2', 166]
[1143, -5.2895000000000003, 2.6755, 'Al2O